In [1]:
import pandas as pd
import matplotlib.pyplot as plt
from py2neo import Graph, Node, Relationship
import nltk
from py2neo import *
import pandas as pd
from pprint import pprint
from nltk import sent_tokenize, word_tokenize
from nltk.corpus import stopwords
import spacy
from spacy import displacy
import en_core_web_sm
from nltk import pos_tag
from itertools import *
import glob
import csv
from gensim.matutils import softcossim
from gensim import corpora
import gensim
import time
import gensim.downloader as api
from gensim.matutils import softcossim
from gensim import corpora
import gensim
from tqdm import tqdm
import warnings
warnings.filterwarnings("ignore")

In [2]:
df = pd.read_csv("C:/Users/wongzn/Desktop/rs_data_coref_nomax.csv")[["relation","subject","object"]]

In [3]:
df.head()

relation                        subject  \
0                 was  21-year-old Malaysian suspect   
1          containing                             he   
2          containing                             he   
3  containing 336g at                             he   
4                 was              Malaysian suspect   

                                  object  
0                               arrested  
1                            336g of Ice  
2                                   336g  
3  carpark in vicinity of Orchard Towers  
4                               arrested

In [4]:
df.relation = df.relation.str.lower()
df.subject = df.subject.str.lower()
df.object = df.object.str.lower()
df.subject = df.subject.replace(regex=['^.*republic polytechnic.*$', ], value='republic polytechnic')
df.subject = df.subject.replace(regex=['^prime minister$','^prime minister lee$','^.*lee hsien loong.*$','^.*pm lee.*$'], value='lee hsien loong')
df.subject = df.subject.replace(regex=['^.*people \'s action party.*$','^.*people \'s assoc.*$','^prime minister \'s office', r'^government$', '^governments$', '^.*government agenc.*$', '^government representatives$', '^minister$','^bministers$', 'preliminary estimates$'], value='singapore government')
df.subject = df.subject.replace(regex=['^.*halimah.*$'], value='president halimah yacob')
df.subject = df.subject.replace(regex=['^.*scdf.*$','^.*civil defence.*$'], value='scdf')
df.subject = df.subject.replace(regex=['^.*the republic.*$','^republic$','republic \'s','singapore \'s','our singapore'], value='singapore')
df.subject = df.subject.replace(regex=['^.*members of public.*$','^public$',r'singapore people', r'^singaporean.*',r'singaporeans','^.*more singaporean.*$','^.*younger singaporean.*$','^.*the singaporean.*$','^.*her singaporean.*$','^.*individual singaporean.*$','^.*eligible singaporean.*$','^.*older singaporean.*$','^.*many singaporean.*$','^.*us singaporean.*$','^.*else singaporean.*$','^.*capable singaporean.*$','^.*fsingaporean.*$','^.*things singaporean.*$','^.*young singaporean.*$','^.*singaporean household.*$'], value='singaporean')
df.subject = df.subject.replace(regex=['^lta$', r'^lta.*$',r'land transport authority','lta enforcement','^lta.*$','the lta.*$','lta \'s.*$','\-lrb\- lta.*$','^.*lta officer.*$','^.*by lta.*$'], value='lta')
df.subject = df.subject.replace(regex=['^.*straits times.*$','^st$','^.*straits\_times.*$'], value='straits times')
df.subject = df.subject.replace(regex=['^.*heng swee keat.*$', '^.*mr heng.*$', '^.*heng$'], value='heng swee keat')
df.subject = df.subject.replace(regex=['^.*police centre.*$',r'local police',r'police units',r'the police',r'criminal investigation department',r'auxiliary police assistance ','^police$','^.*police offic.*$','^.*policem.n.*$','^.*police hotline.*$','^.*police division.*$','police officer \'s','^.*police force.*$','^.*police spokesm.n.*$','^.*police personnel.*$','^.*police advisory.*$'], value='singapore police force')
df.subject = df.subject.replace(regex=['^.*police report.*$','^.*police investigation.*$'], value='police report')
df.subject = df.subject.replace(regex=['^.*police vehicle.*$','^.*police van.*$','^.*police car.*$'], value='police vehicle')
df.subject = df.subject.replace(regex=['^.*cnb.*$', '^.*central narcotics.*$' ], value='central narcotics bureau')
df.subject = df.subject.replace(regex=['^.*armenian prime.*$' ], value='armenian prime minister nikol pashinyan')
df.subject = df.subject.replace(regex=['^.*mahathir mohamad.*$' ], value='mahathir mohamad')
df.subject = df.subject.replace(regex=['^.*singapore general hospital.*$', '^general hospital$' ], value='singapore general hospital')
df.subject = df.subject.replace(regex=['^hospitals$','^.*local hospital.*$','^.*other hospital.*$','^.*private hospital.*$','^.*in hospital.*$' ], value='hospital')
df.subject = df.subject.replace(regex=['^.*children \'s hospital.*$','^.*kk women \'s hospital.*$','^\'s hospital' ], value='hospital')
df.subject = df.subject.replace(regex=['^.*this year.*$' ], value='2019')
df.subject = df.subject.replace(regex=['^.*last year.*$' ], value='2018')
df.subject = df.subject.replace(regex=['^.*south china sea.*$' ], value='south china sea')
df.subject = df.subject.replace(regex=['^.*china \'s economy.*$','^.*business china.*$','^.*thinkchina.*$', '^.*china \'s own policies.*$','^.*china of doing.*$','^.*led china.*$','^.*china \'s military actions .*$','^.*china \'s growth.*$','^.*china government.*$','^.*china \'s.*$','^.*china \'s unfriendly behaviour.*$','petrochina'], value='china')
df.subject = df.subject.replace(regex=['^.*china taiping.*$','^.*business china.*$','^.*thinkchina.*$'], value='china taiping insurance')
df.subject = df.subject.replace(regex=['^.*trade war.*$','^.*trade dispute.*$','^.*us\-china tariffs.*$'], value='us china trade war')
df.subject = df.subject.replace(regex=['^.*us\-china.*$','^.*us and china.*$', '^.*united states and china.*$','^.*us regard china.*$'], value='us china trade war')
df.subject = df.subject.replace(regex=['^patients.*$'], value='patient')
df.subject = df.subject.replace(regex=['^.*fake article.*$','^.*bogus article.*$','^.*fake new.*$','^.*fake online.*$'], value='fake news')
df.subject = df.subject.replace(regex=['^.*fires.*$','^the fire$','^.*other fires.*$','^.*fake online.*$','^a fire$','^large fire.*$'], value='fire')
df.subject = df.subject.replace(regex=['^.*national environment agency.*$','^.*nea offic.*$','^.*nea spokes.*$', '^.*nea \'s.*$','^.*nea survey.*$','^.*nea website.*$','^.*nea enforcement.*$'], value='nea')
df.subject = df.subject.replace(regex=['^court$','^high court$','^.*court of appeal.*$', '^.*state courts.*$','^.*courtroom.*$','^.*highest court.*$','^.*the permanent court.*$','^.*district court.*$','^supreme court$','^.*singapore high court.*$'], value='singapore court')
df.subject = df.subject.replace(regex=['^indian supreme court$','^india \'s supreme court $', '^.*indian court.*$','^.*supreme court of india.*$'], value='india court')
df.subject = df.subject.replace(regex=['^.*court case.*$','^.*court proce.*$', '^.*court hearing.*$'], value='court cases')
df.subject = df.subject.replace(regex=['^.*mrs teo.*$','^.*josephine teo.*$','^.*manpower minister teo.*$'], value='josephine teo')
df.subject = df.subject.replace(regex=['^.*teo chee hean.*$'], value='teo chee hean')
df.subject = df.subject.replace(regex=['^.*events$','^.*other event.*$','^.* \'s event.*$'], value='event')
df.subject = df.subject.replace(regex=['^.*cpl kok$','^.*kok yuen chin.*$'], value='kok yuen chin')
df.subject = df.subject.replace(regex=['^.*tan kin lian.*$'], value='tan kin lian')
df.subject = df.subject.replace(regex=['^.*tan eng.*$'], value='tan eng kun')
df.subject = df.subject.replace(regex=['^.*tan kok tiong.*$'], value='tan kok tiong')
df.subject = df.subject.replace(regex=['^.*education minister ong$','^.*ong ye kung.*$'], value='ong ye kung')
df.subject = df.subject.replace(regex=['^.*goh chok tong.*$','^.*emeritus senior.*$','^.*esm goh.*$'], value='goh chok tong')
df.subject = df.subject.replace(regex=['^.*lawrence wong.*$'], value='lawrence wong')
df.subject = df.subject.replace(regex=['^mo kio$','^.*kio avenue.*$','^.*kio mrt.*$','^.*kio park.*$','^.*ang mo kio.*$','^.*kio garden.*$'], value='ang mo kio')
df.subject = df.subject.replace(regex=['^.*kio grc.*$','^.*kio community.*$''^.*kio town.*$'], value='ang mo kio grc')
df.subject = df.subject.replace(regex=['^.*ministry of manpower.*$','^mom$','^.*manpower ministry.*$'], value='ministry of manpower')
df.subject = df.subject.replace(regex=['^.*ministry of education.*$','^moe$','^.*education ministry.*$'], value='ministry of education')
df.subject = df.subject.replace(regex=['^.*ministry of health.*$','^moh$','^.*health ministry.*$'], value='ministry of health')
df.subject = df.subject.replace(regex=['^.*ministry of defence.*$',r'mindef','^.*defence ministry.*$'], value='ministry of defence')
df.subject = df.subject.replace(regex=['^.*ministry of social.*$','^msf$'], value='ministry of social and family development')
df.subject = df.subject.replace(regex=['^.*ministry of foreign affairs.*$','^mfa$','^.*foreign ministry.*$'], value='ministry of foreign affairs')
df.subject = df.subject.replace(regex=['^.*ministry of home affair.*$','^mha$'], value='ministry of home affairs')
df.subject = df.subject.replace(regex=['^.*ministry of finance.*$','^.*ministry of economy.*$','^.*finance ministry.*$','^mof$'], value='ministry of finance')
df.subject = df.subject.replace(regex=['^.*ministry of transport.*$','^.*transport ministry.*$','mot$'], value='ministry of transport')
df.subject = df.subject.replace(regex=['^.*ministry of law.*$','^.*law ministry.*$'], value='ministry of law')
df.subject = df.subject.replace(regex=['^.*ministry of transport.*$','^.*transport ministry.*$','mot$'], value='ministry of transport')
df.subject = df.subject.replace(regex=['^.*ministry of the environment and water resources.*$','^.*ministry of environment and water resources.*$'], value='ministry of environment and water resources')
df.subject = df.subject.replace(regex=['^.*ministry for trade and industry.*$','^.*ministry of trade and industry.*$','^mti$','^.*trade and industry ministry.*$'], value='ministry of trade and industry')
df.subject = df.subject.replace(regex=['^.*ministry for trade and industry.*$','^.*ministry of trade and industry.*$','^mti$','^.*trade and industry ministry.*$'], value='ministry of trade and industry')
df.subject = df.subject.replace(regex=['^pub$','^pub \'s$','^pub water.*$','^.*public utilities board.*$'], value='public utilities board')
df.subject = df.subject.replace(regex=['^nus$','^.*national university of singapore.*$','^.*university of singapore.*$','^.*yale\-nus.*$','^.*nus students.*$','^nus disciplinary board$','^.*duke\-nus.*$','^.*nus dentistry.*$', '^.*nus spokesman.*$', '^.*nus \-rrb\- business school*$', '^.*nus board.*$', '^.*one nus.*$','^.*nus management.*$','^.*nus medicine.*$','^.*students and staff at nus.*$','^.*nussu.*$'], value='public utilities board')
df.subject = df.subject.replace(regex=['^dr ng on matter$','^.*dr ng \'s visit.*$','^.*yale\-nus.*$','^.*dr ng junior college.*$','^alphonsus chern dr ng$','^.*dr ng \'s last visit.*$'], value='dr ng')
df.subject = df.subject.replace(regex=['^.*ng eng hen.*$'], value='ng eng hen')
df.subject = df.subject.replace(regex=['^.*singapore management university.*$','^.*\-lrb\- smu \-rrb\-.*$'], value='singapore management university')
df.subject = df.subject.replace(regex=['^.*nanyang technological university.*$','^.*\-lrb\- ntu \-rrb\-.*$'], value='singapore management university')
df.subject = df.subject.replace(regex=['^.*lianhe wanbao.*$','^.*wanbao.*$'], value='lianhe wanbao')
df.subject = df.subject.replace(regex=['^.*lianhe zaobao.*$','^.*zaobao.*$'], value='lianhe zaobao')
df.subject = df.subject.replace(regex=['^.*sbs.*$'], value='sbs transit')
df.subject = df.subject.replace(regex=['^.*warren fernandez.*$'], value='warren fernandez')
df.subject = df.subject.replace(regex=['^.*health sciences authority.*$','^.*hsa.*$'], value='health sciences authority')
df.subject = df.subject.replace(regex=['^.*grace goh.*$'], value='grace goh')
df.subject = df.subject.replace(regex=['^.*shanmugam.*$'], value='k. shanmugam')
df.subject = df.subject.replace(regex=['^.*smrt.*$'], value='smrt')
df.subject = df.subject.replace(regex=['^polytechnics.*$'], value='polytechnics')
df.subject = df.subject.replace(regex=['^.*ann polytechnic.*$'], value='ngee ann polytechnic')
df.subject = df.subject.replace(regex=['^.*temasek polytechnic.*$'], value='temasek polytechnic')
df.subject = df.subject.replace(regex=['^.*nanyang polytechnic.*$', ], value='nanyang polytechnic')
df.subject = df.subject.replace(regex=['^.*singapore polytechnic.*$', ], value='singapore polytechnic')
df.subject = df.subject.replace(regex=['^.*psi.*$', ], value='24-hour psi')
df.subject = df.subject.replace(regex=['^.*expensive resale.*$','^.*resale market.*$','^.*hdb resale.*$', '^.*resale flat.*$','^.*resale price.*$','^.*resale vol.*$','^.*resale tran.*$'], value='hdb resale')
df.subject = df.subject.replace(regex=['^.*hdb owners.*$','^.*hdb flat owners.*$'], value='hdb owners')
df.subject = df.subject.replace(regex=['^hdb$','^.*hdb house.*$','^.*hdb data.*$','^.*hdb flat.*$','^.*hdb hub.*$','^.*hdb estate.*$'], value='hdb')
df.subject = df.subject.replace(regex=['^.*khaw boon wan.*$','^.*khaw.*$'], value='khaw boon wan')
df.subject = df.subject.replace(regex=['^student$','^students$','^most students$','^lower students$','^our students$'], value='students')
df.subject = df.subject.replace(regex=['^.*shin min.*$'], value='shin min daily news')
df.subject = df.subject.replace(regex=['^sph .*$','^.*singapore press holdings.*$'], value='singapore press holdings')
df.subject = df.subject.replace(regex=['^.*scammer.*$'], value='scammer')
df.subject = df.subject.replace(regex=['^.*shanahan.*$'], value='patrick shanahan')
df.subject = df.subject.replace(regex=['^.*visvanathan.*$'], value='visvanathan vadivelu')
df.subject = df.subject.replace(regex=['^.*singapore food agency.*$', '^.*sfa.*$'], value='singapore food agency')
df.subject = df.subject.replace(regex=['^sands.*$', '^.*marina bay sand.*$'], value='marina bay sands')
df.subject = df.subject.replace(regex=['^.*cfc pang.*$', '^.*aloysius pang.*$','^.*mr pang 24.*$'], value='aloysius pang')
df.subject = df.subject.replace(regex=['^ica$', '^.*immigration and checkpoints.*$'], value='immigration and checkpoints authority')
df.subject = df.subject.replace(regex=['^.*donald trump.*$','^.*mr trump.*$','^trump$','^.*trump admin.*$'], value='donald trump')

def preprocess_content(column):
    column = column.apply(lambda x: re.sub(r'\d{2}[/-]\w{4}[/-]\w{3,4}', '',x)) #remove(xx-year-old)
    column = column.apply(lambda x: re.sub(r'^mr$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^ms$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^miss$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^dr$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^prof$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^mrs$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^mdm$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^madam$','',x, flags=re.IGNORECASE))
    #column = column.apply(lambda x: re.sub(r'[^a-zA-z\s]', ' ', x)) #removing digits and special characters (punctuations)
    return column

df['subject'] = preprocess_content(df['subject'])

def preprocess_object(column):
    #column = column.apply(lambda x: re.sub(r'\d{2}[/-]\w{4}[/-]\w{3,4}', '',x)) #remove(xx-year-old)
    column = column.apply(lambda x: re.sub(r'^mr$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^ms$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^miss$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^dr$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^prof$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^mrs$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^mdm$','',x, flags=re.IGNORECASE))
    column = column.apply(lambda x: re.sub(r'^madam$','',x, flags=re.IGNORECASE))
    #column = column.apply(lambda x: re.sub(r'[^a-zA-z\s]', ' ', x)) #removing digits and special characters (punctuations)
    return column

df['object'] = preprocess_content(df['object'])

df.subject = df.subject.replace(regex=['^.*lee kuan.*$'], value='lee kuan yew')
df.subject = df.subject.replace(regex=['^.*hng kiang.*$'], value='lim hng kiang')
df.subject = df.subject.replace(regex=['^.*su aun.*$'], value='jeffrey ong su aun')
df.subject = df.subject.replace(regex=['^.*kok keong.*$'], value='ong kok keong')
df.subject = df.subject.replace(regex=['^.*heng chuan.*$'], value='ong heng chuan')
df.subject = df.subject.replace(regex=['^.*hng kiang.*$'], value='lim hng kiang')
df.subject = df.subject.replace(regex=['^.*mr ngu.*$', '^.*michael ngu.*$'], value='mr ngu')
df.subject = df.subject.replace(regex=['^.*bao hui.*$'], value='ng bao hui')
df.subject = df.subject.replace(regex=['^.*hng kiang.*$'], value='lim hng kiang')
df.subject = df.subject.replace(regex=['^.*mr nigam.*$'], value='mr nigam')
df.subject = df.subject.replace(regex=['^.*diana ngiam.*$'], value='diana nigam')
df.subject = df.subject.replace(regex=['^.*ng kong yeam.*$'], value='ng kong yeam')
df.subject = df.subject.replace(regex=['^.*wong zi heng.*$'], value='wong zi heng')
df.subject = df.subject.replace(regex=['^.*tang yian.*$'], value='ang tang yian')
df.subject = df.subject.replace(regex=['^.*iswaran.*$'], value='s. iswaran')
df.subject = df.subject.replace(regex=['^.*beng yeow.*$'], value='goh beng yeow')
df.subject = df.subject.replace(regex=['^.*mr pang 24.*$'], value='aloysius pang')
df.subject = df.subject.replace(regex=['^.*masagos.*$'], value='masagos zulkifli')
df.subject = df.subject.replace(regex=['^.*chiap shing.*$'], value='chin chiap shing')
df.subject = df.subject.replace(regex=['^.*guat kwang.*$'], value='yeo guat kwang')
df.subject = df.subject.replace(regex=['^.*yipeng.*$'], value='li yipeng')
df.subject = df.subject.replace(regex=['^.*luhut.*$'], value='mr luhut')
df.subject = df.subject.replace(regex=['^.*hong tat.*$','^.*chee hong.*$'], value='chee hong tat')
df.subject = df.subject.replace(regex=['^.*tsang wai.*$','^.*mr tsang.*$'], value='andy tsang wai hung')
df.subject = df.subject.replace(regex=['^.*muhammad rilwan.*$'], value='muhammad rilwan')
df.subject = df.subject.replace(regex=['^.*toon ouut.*$'], value='wee toon ouut')
df.subject = df.subject.replace(regex=['^.*pan lee.*$'], value='wee pan lee')
df.subject = df.subject.replace(regex=['^.*pashinyan.*$'], value='nikol pashinyan')
df.subject = df.subject.replace(regex=['^.*peng chye.*$','^.*mr swee.*$'], value='swee pwng chye')
df.subject = df.subject.replace(regex=['^.*khairil.*$'], value='khairil tahir')
df.subject = df.subject.replace(regex=['^.*zaqy.*$'], value='zaqy mohamad')
df.subject = df.subject.replace(regex=['^.*alex yeung.*$'], value='alex yeung')
df.subject = df.subject.replace(regex=['^.*mr mah.*$','^.*kiat seng.*$'], value='mah kiat seng')
df.subject = df.subject.replace(regex=['^.*zainal.*$'], value='zainal sapari')
df.subject = df.subject.replace(regex=['^.*arora neil.*$'], value='arora neil kant')
df.subject = df.subject.replace(regex=['^.*mr quak.*$','^.*kelvin quak.*$'], value='kelvin quak')
df.subject = df.subject.replace(regex=['^.*mr chiam.*$','^.*chiam see tong.*$'], value='chiam see tong')
df.subject = df.subject.replace(regex=['^.*tharman.*$'], value='tharman shanmugaratnam')
df.subject = df.subject.replace(regex=['^.*eugene seah.*$'], value='eugene seah')
df.subject = df.subject.replace(regex=['^.*seah kian peng.*$'], value='seah kian peng')
df.subject = df.subject.replace(regex=['^.*guoyuan.*$'], value='zeng guoyuan')
df.subject = df.subject.replace(regex=['^.*amrin amin.*$','^.*mr amrin.*$'], value='amrin amin')
df.subject = df.subject.replace(regex=['^.*gabriel choy.*$'], value='gabriel choy')
df.subject = df.subject.replace(regex=['^.*sundaresh menon.*$','^.*cj menon.*$','^.*justice menon.*$','^.*mr menon.*$'], value='sundaresh menon')
df.subject = df.subject.replace(regex=['^.*hanwei.*$'], value='lin hanwei')
df.subject = df.subject.replace(regex=['^.*mr kuek 55.*$'], value='mr kuek')
df.subject = df.subject.replace(regex=['^.*kaesang.*$'], value='kesang pangarep')
df.subject = df.subject.replace(regex=['^.*lawrence tan.*$'], value='lawrence tan')
df.subject = df.subject.replace(regex=['^.*azahari.*$'], value='mohamamad azahari abdul razak')
df.subject = df.subject.replace(regex=['^.*seng yap.*$'], value='peng seng yap')
df.subject = df.subject.replace(regex=['^.*aizat.*$'], value='aizat hashim')
df.subject = df.subject.replace(regex=['^.*hoyu.*$'], value='eric chong hoyu')
df.subject = df.subject.replace(regex=['^.*jayachandran.*$'], value='r. jayachandran')
df.subject = df.subject.replace(regex=['^.*murjani.*$'], value='murjani')
df.subject = df.subject.replace(regex=['^.*yusoff hashim.*$'], value='mohamed yusoff hashim')
df.subject = df.subject.replace(regex=['^.*qwong meng.*$'], value='qwong meng')
df.subject = df.subject.replace(regex=['^.*cory wong.*$'], value='cory wong')
df.subject = df.subject.replace(regex=['^.*beng yeow.*$'], value='goh beng yeow')
df.subject = df.subject.replace(regex=['^.*haikal johari.*$','^.*mr haikal.*$','^.*chef haikal.*$'], value='muhammad haikal johari')
df.subject = df.subject.replace(regex=['^.*al baker.*$'], value='al baker')
df.subject = df.subject.replace(regex=['^.*sikri.*$'], value='arjan kumar sikri')
df.subject = df.subject.replace(regex=['^.*christopher monteiro.*$'], value='christopher monteiro')
df.subject = df.subject.replace(regex=['^.*ramesh tiwary.*$'], value='ramesh tiwary')
df.subject = df.subject.replace(regex=['^.*justice ramesh.*$','^.*justice kannan.*$'], value='kannan ramesh')
df.subject = df.subject.replace(regex=['^.*kyriakou.*$'], value='kyriakou')
df.subject = df.subject.replace(regex=['^.*tan hsiao tien.*$'], value='tan hsiao tien')
df.subject = df.subject.replace(regex=['^.*desmond lee.*$'], value='desmond lee')
df.subject = df.subject.replace(regex=['^.*joko.*$'], value='joko widodo')
df.subject = df.subject.replace(regex=['^.*nafiz.*$'], value='nafiz kamarudin')
df.subject = df.subject.replace(regex=['^.*gajendran.*$'], value='gajendran ramesh')
df.subject = df.subject.replace(regex=['^.*richard poh.*$'], value='richard poh')
df.subject = df.subject.replace(regex=['^.*sojie singh.*$'], value='sojit singh')
df.subject = df.subject.replace(regex=['^.*gibran.*$'], value='gibran')
df.subject = df.subject.replace(regex=['^.*ho chew.*$'], value='foo ho chew')
df.subject = df.subject.replace(regex=['^.*imran kassim.*$'], value='imran kassim')
df.subject = df.subject.replace(regex=['^.*louis pang.*$'], value='louis pang')
df.subject = df.subject.replace(regex=['^.*andy png.*$'], value='andy png')
df.subject = df.subject.replace(regex=['^.*jeremy tong.*$'], value='jeremy tong')

words_to_exclude = ['it','he','man','we','they','people','she','officers', 'woman','his','those','you','the','men','boy','her','group','centre','ban','i','person','their','girl','our','women','conditions','some','participants','exercise','one','this','anyone','photo','two','others','its','note','other','measures','half','many','year','him','efforts','amount','changes','move','st photo','respondents','agreement','work','proportion','more','recommendations','father','all','use','them','board','activities','cent','part','weekend','typical weekend','streets','plan','time','design','statement','mother','course','details','features','everyone','issues','terms','operators','products','acts','another','series','scheme','line','works','substances','everything','partners','rise','ad','mr','survey','unit','first','trust','demand','sit','low','opportunities','post','devices','way','experts','process','site','sides','here','things','son','impact','friends','tender','$ sum','guests','areas','challenges','list','operations','both','village','latter','arrangements','act','sections','spending','total','someone','charge','most','items','experience','care','third','many people','collaboration','deadline','jobs','hurt','innovation','stories','nothing','images','my','something','place','matter','rates','phase','latest','questions','decision','total number','per cent','action','tests','roads','picture','story','space','issue','differences','section','term','ways','cause','show','tree','special','index','three','six','set','wrs','me','signs','skills','content','himself','each','stretch','clips','sector','systems','notes','age','stage','opening','flyer','estates','effects','spots','clip','point','challenge','access','need','lifts','step','rest','name','session','fact','repairs','product','reading',"'s",'points','package','symptoms','head','interviews','there','office','author','decrease','passers-by','month','snake','size','help','ye','crabs','column','batch','cracks','callers','cooperation','bag','that','trail','spot','kale','idea','block','balance','new building','claim','shop','outlets','research','an','amendments','route','methods','buyer','problem','call','spell','weight','boys','lack','conditon','operator','record','base','letters','scale','her son','proceeds','quarter','your','role','premises','few days','level','flag','releases','appropriateness','displays','raising','folders','rate','search','interest','such initiatives','relative','highlights','link','division','cost','grouping','few friends','option','structure','power','bridges','approach','plant','their apology','she posts','supply','steps','score','going','talk','objects','best','moves','discussion','item','cc', 'views','retno','numbers','cards','recall','sites','run','blaze','viewers','outlet','having','then','little boy','spaces','examples','tel','living','hit','none','towers','mothers','a','tang','range','much','sales','paper','papers','effort','ones','kids','drive','identities','crutch','nephew','signing','walk','interior','journey','room','and','boxes','mover','news','member','trip','block numbers','hours','procedure','times','last','digital','caller','books','stamp','night','months','donations','networks','banch','taking','visit','chain','ride','brother','result','visibility','such cases','bookings','practice','inputs','knife','aim','projection','ties','waterspout','parent','ms','scene','collection','seat','second','difference','page']

df = df[~df.subject.isin(words_to_exclude)]

# Cleaning Relations Data

In [5]:
df.drop_duplicates(inplace=True) #dropping duplicated relations
df.reset_index(drop=True,inplace=True)
df.all = df.relation + ' ' + df.subject +' '+ df.object

In [6]:
fasttext_model300 = api.load('fasttext-wiki-news-subwords-300')

In [7]:
documents = df.all.apply(lambda x: x.split())
dictionary = corpora.Dictionary(documents)

In [8]:
st=time.time()
similarity_matrix = fasttext_model300.similarity_matrix(dictionary, tfidf=None, threshold=0.0, exponent=2.0, nonzero_limit=100)
time.time()-st

2698.08948802948

In [9]:
sentences = documents.apply(lambda x: dictionary.doc2bow(x))
sent = pd.DataFrame(sentences)

In [10]:
#Loop through Relations data, remove Relations that are similar

index = []
st = time.time()

for i in tqdm(range(len(sent))):
    if i not in index:
        for j in range(15):
            scs = softcossim(sent[0][i],sent[0][i+j+1],similarity_matrix)
            if scs > 0.75: #Threshold
                len1 = len(sent[0][i])
                len2 = len(sent[0][i+j+1])
                if len1 > len2: #Getting index of the shorter relation
                    index.append(i+j+1)
                else:
                    index.append(i)
            else:
                continue
    else: 
        continue

100%|████████████████████████████████████████████████████████████████████████▉| 263018/263046 [28:35<00:00, 125.75it/s]

KeyError: 263046

100%|████████████████████████████████████████████████████████████████████████▉| 263018/263046 [28:50<00:00, 125.75it/s]

In [11]:
print(time.time()-st)

2360.408665895462


In [12]:
index = list(set(index))
df.drop(index,axis=0,inplace=True) #Removing Relations that are similar and shorter in length
df.reset_index(drop=True,inplace=True)

In [13]:
df.drop_duplicates(inplace=True) #Drop duplicates again just in case

In [14]:
df = df[['relation','subject','object']]

In [15]:
df['subject'] = df['subject'].apply(lambda x: re.sub('\n','',x))

In [16]:
#Get unique subjects
subj = df.subject.unique()

In [17]:
len(subj)

29466

In [31]:
#df.to_csv("C:/Users/wongzn/Desktop/df_backupafterprocess.csv")

# Further Cleaning of Relations By Subject

In [50]:
subj_1 = subj[:9879]
subj_2 = subj[9879:14879]
subj_3 = subj[14879:19879]
subj_4 = subj[19879:24879]
subj_5 = subj[24879:]

In [19]:
#final_df = pd.DataFrame(columns=['relation','subject','object'])

for s in tqdm(subj):
    new_df = df[df.subject == s]
    new_df.reset_index(inplace=True,drop=True)
    new_df.all = new_df.relation + ' ' + new_df.subject +' '+ new_df.object
    documents = new_df.all.apply(lambda x: x.split())
    dictionary = corpora.Dictionary(documents)
    similarity_matrix = fasttext_model300.similarity_matrix(dictionary, tfidf=None, threshold=0.0, exponent=2.0, nonzero_limit=100)
    sentences = documents.apply(lambda x: dictionary.doc2bow(x))
    sent = pd.DataFrame(sentences)
    index = []
    for i in range(len(sent)):
        if i not in index:
            for j in range(5):
                try:
                    scs = softcossim(sent[0][i],sent[0][i+j+1],similarity_matrix)
                    if scs > 0.75:
                        len1 = len(sent[0][i])
                        len2 = len(sent[0][i+j+1])
                        if len1 > len2:
                            index.append(i+j+1)
                        else:
                            index.append(i)
                            
                except:
                    continue
    index = list(set(index))
    new_df.drop(index,axis=0,inplace=True)
    final_df = final_df.append(new_df, ignore_index=True)


  0%|▏                                                                           | 67/29466 [12:32<22:00:31,  2.70s/it]


  0%|▎                                                                          | 135/29466 [24:44<92:59:20, 11.41s/it]


  1%|▌                                                                          | 203/29466 [35:01<66:02:14,  8.12s/it]


  1%|▋                                                                          | 271/29466 [42:14<31:24:25,  3.87s/it]


  1%|▊                                                                         | 339/29466 [51:09<189:17:35, 23.40s/it]


...

 99%|████████████████████████████████████████████████████████████████████████▍| 29239/29466 [13:47:40<04:55,  1.30s/it]


 99%|████████████████████████████████████████████████████████████████████████▌| 29307/29466 [13:49:08<04:16,  1.61s/it]


100%|████████████████████████████████████████████████████████████████████████▊| 29375/29466 [13:50:31<01:28,  1.03it/s]


100%|████████████████████████████████████████████████████████████████████████▉| 29443/29466 [13:52:14<00:25,  1.13s/it]


100%|█████████████████████████████████████████████████████████████████████████| 29466/29466 [13:52:44<00:00,  1.29s/it]

In [20]:
final_df

relation  \
0                                                 was   
1                                               is in   
2                                               is in   
3                                               is in   
4                                               is in   
5                                               is in   
6                                               is in   
7                                                  be   
8                                               is in   
9                                    from officers is   
10                                     also recovered   
11                                            said in   
12                                                 of   
13                                   is investigating   
14                                            said in   
15                                    arrested man in   
16                   also arrested drug trafficker at   
17                                           reminded   
18                                             tailed   
19                                    recovered about   
20                                            said on   
21                             cited june report from   
22                                              cited   
23                                        seize drugs   
24                                             seized   
25                                also raided unit in   
26                                           arrested   
27                                           included   
28                                   is investigating   
29                                              is in   
...                                               ...   
85908                                    is headed by   
85909                                           is in   
85910                                    reach out to   
85911                        provide opportunities to   
85912                                              is   
85913  discharge deputy public prosecutor winston man   
85914                                    adjourn case   
85915                                            gave   
85916                               sexually violated   
85917                                         is with   
85918                                   was sentenced   
85919                                             was   
85920                                        pleading   
85921                                            left   
85922                               returned later to   
85923                                           is in   
85924                          alerted police at_time   
85925                                       ' unit is   
85926                                   of officer is   
85927                                      threatened   
85928                                           is in   
85929                                             was   
85930                                           is in   
85931                                          can co   
85932                           exists extensively in   
85933                           exists extensively in   
85934                         can also cause surge in   
85935                                         driving   
85936                                  can also cause   
85937                  are non-human primates such as   

                                                 subject  \
0                                      malaysian suspect   
1                                                carpark   
2                                                carpark   
3                                                carpark   
4                                                carpark   
5                                                carpark   
6                                                carpark   
7                             

In [26]:
#FINAL = pd.DataFrame(columns=['relation','subject','object'])
#FINAL = FINAL.append(final_df, ignore_index=True)
#final_df.to_csv("C:/Users/wongzn/Desktop/Final_Cleaned_Relations.csv")

In [21]:
import numpy as np
final_df['subject'].replace('', np.nan, inplace=True)
final_df['subject'].replace(' ', np.nan, inplace=True)
final_df['subject'].replace('  ', np.nan, inplace=True)
final_df['subject'].replace('   ', np.nan, inplace=True)
final_df['subject'].replace('    ', np.nan, inplace=True)
final_df['subject'].replace('     ', np.nan, inplace=True)
final_df['subject'].replace('      ', np.nan, inplace=True)
final_df['subject'].replace('       ', np.nan, inplace=True)
final_df['subject'].replace('        ', np.nan, inplace=True)
final_df['subject'].replace('         ', np.nan, inplace=True)
final_df['subject'].replace('          ', np.nan, inplace=True)
final_df['subject'].replace('           ', np.nan, inplace=True)
final_df['subject'].replace('            ', np.nan, inplace=True)

In [22]:
final_df['subject'].dropna(inplace=True)
final_df['subject'] = final_df['subject'].apply(lambda x: x.strip())

In [25]:
sum(final_df.subject.value_counts()>3)

3694

In [24]:
final_df.drop_duplicates(inplace=True)

# Importing into Neo4j

In [27]:
import nltk
from py2neo import *
import pandas as pd
from pprint import pprint
from nltk import sent_tokenize, word_tokenize
from nltk.corpus import stopwords
import spacy
from spacy import displacy
import en_core_web_sm
from nltk import pos_tag
from itertools import *
import glob
import csv
from py2neo import Graph, Node, Relationship

In [28]:
graph = Graph('bolt://localhost:7687', auth=("neo4j","123"))
tx = graph.begin()

In [29]:
subject_df = list(final_df.subject.unique())

In [36]:
for i in subject_df:
    new_df = final_df[final_df.subject == i]
    new_df.reset_index(drop=True,inplace=True)
    N1 = Node("Subject", subj=i)
    #tx.merge(N1,"dat","data")
    for row in range(len(new_df)):
        N2 = Node("Object", obj=new_df.object[row])
        #tx.merge(N2,"Object","obj")
        rel = Relationship(N1, new_df.relation[row], N2)
        graph.create(rel)

# Steps to set up Neo4j

1. Download GraphAware files (for NLP): https://products.graphaware.com/
        - Installing GA on Neo4j: https://github.com/graphaware/neo4j-nlp
2. Download StanfordCoreNLP Jar file: https://stanfordnlp.github.io/CoreNLP/download.html
3. Install APOC Plugin on Neo4j
4. Run the above Python code and Neo4j Query to merge the nodes

 # Neo4j Codes

### Running this query will give us the following:

![Querying A Specific Subject](https://user-images.githubusercontent.com/36468263/77022937-d1598480-69c5-11ea-9862-51e881071495.jpg)

In [ ]:
Double click to Expand

![Expanding A Particular Node By Double Clicking](https://user-images.githubusercontent.com/36468263/77022939-d28ab180-69c5-11ea-9e54-6ef75fa6011f.jpg)

In [ ]:
Double click on PM

![Subjects Linked To Prime Ministers](https://user-images.githubusercontent.com/36468263/77022942-d3234800-69c5-11ea-8862-1975e3f02c4e.jpg)

In [ ]:
Double Click on Jewel

![Expanding Jewel Changi](https://user-images.githubusercontent.com/36468263/77022850-9ce5c880-69c5-11ea-8eee-112f6553584f.jpg)

### To Query For Relations